In [ ]:
#preprocessing libriaris
import nltk
nltk.download("stopwords")
#stopwords modules
from nltk.corpus import stopwords
from pymystem3 import Mystem
from string import punctuation

In [5]:
#Create lemmatizer and stopwords list
mystem = Mystem() 
russian_stopwords = stopwords.words("russian")

#Preprocess function (stopwords, puncuation, etc)
def preprocess_text(text):
    tokens = mystem.lemmatize(text.lower())
    tokens = [token for token in tokens if token not in russian_stopwords\
              and token != " " \
              and token.strip() not in punctuation]
    
    text = " ".join(tokens)
    
    return text

#Examples    
preprocess_text("<|startoftext|>Выкинь все, что есть в твоих мыслях: грусть, пустоту, печаль. Помнишь, как ты подарил мне лето, в то время, как был февраль.<|endoftext|>")

'<| startoftext |> выкидывать твой мысль грусть пустота печаль помнить подарить лето время февраль <| endoftext |>\n'

In [6]:
import pandas as pd
import numpy as np
import io

qoute_path = '../parsing/data/cleaned_tagged.txt'

df = pd.read_csv(qoute_path, sep='<\d*>', engine ='python', names=['quotes']) #reading quotes to the dataframe
with open(qoute_path, 'r', encoding='utf-8') as file:
    data = file.read().replace('\n', ' nextquote ')
    processed_data = preprocess_text(data)  #preprocessing qoutes
#dataframe with quotes and their processed versions
df.insert(loc=1, column="processed_quotes", value=processed_data.split('nextquote')[:-1], allow_duplicates=True) 

In [7]:
df

quotes  \
0      Выкинь все, что есть в твоих мыслях: грусть, п...   
1      Порой молчание, красноречивее любых произнесен...   
2      А вы знаете, жизнь ведь замечательна и удивите...   
3                              - А че он такой красивый?   
4      Не тот велик, кто никогда не падал, а тот вели...   
...                                                  ...   
12522  Величайшая твердость и есть величайшее милосер...   
12523   Ничто великое в мире не совершается без страсти.   
12524                           Бог рад нечетному числу.   
12525             Иные утверждают, что душа есть воздух.   
12526  Писатель существует только тогда, когда тверды...   

                                        processed_quotes  
0      выкидывать твой мысль грусть пустота печаль по...  
1       пора молчание красноречиво любой произносить ...  
2       знать жизнь замечательный удивительный услови...  
3                                           че красивый   
4                большой падать большой падать вставать   
...                                                  ...  
12522              великий твердость великий милосердие   
12523             ничто великий мир совершаться страсть   
12524                            бог рад нечетный число   
12525                       иной утверждать душа воздух   
12526           писатель существовать твердый убеждение   

[12527 rows x 2 columns]

In [9]:
quote_tokens = [q.split() for q in df['processed_quotes'].values.tolist()]
quote_words = [q.split() for q in df['quotes'].values.tolist()]

#print(quote_tokens[0])
#print(quote_words[0])

In [18]:
import gensim
from gensim.models import Word2Vec
# define a model with parameters
# and train it on our data
model_w2v = Word2Vec(quote_tokens, # data for model to train on
                 vector_size=32,         # embedding vector size
                 min_count=5,     # consider words that occured at least 5 times
                 window=3,
                 hs = 1).wv     # define context as a 3-word window around the target word

In [11]:
wordic ='мама'
model_w2v.get_vector(wordic)
model_w2v.most_similar(wordic)

print(len(model_w2v.index_to_key))

2680


In [12]:
n_words = 1000
words = model_w2v.index_to_key
word_vectors = [model_w2v.get_vector(word) for word in words]

In [13]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

pca = PCA(n_components=32)
pca.fit(word_vectors)
word_vectors_pca = pca.transform(word_vectors)
ss = StandardScaler().fit(word_vectors_pca)
word_vectors_pca = ss.transform(word_vectors_pca)

In [105]:
import bokeh.models as bm, bokeh.plotting as pl
from bokeh.io import output_notebook
output_notebook()

def draw_vectors(x, y, radius=10, alpha=0.25, color='blue',
                 width=600, height=400, show=True, **kwargs):
    if isinstance(color, str): color = [color] * len(x)
    data_source = bm.ColumnDataSource({ 'x' : x, 'y' : y, 'color': color, **kwargs })

    fig = pl.figure(active_scroll='wheel_zoom', width=width, height=height)
    fig.scatter('x', 'y', size=radius, color='color', alpha=alpha, source=data_source)

    fig.add_tools(bm.HoverTool(tooltips=[(key, "@" + key) for key in kwargs.keys()]))
    if show: pl.show(fig)
    return fig


draw_vectors(word_vectors_pca[:, 0], word_vectors_pca[:, 1], token=words)

Loading BokehJS ...

Figure(id='1514', ...)

In [28]:
from sklearn.manifold import TSNE

tsne = TSNE(n_components=2, verbose=32)
#tsne.fit(word_vectors)
word_vectors_tsne = tsne.fit_transform(word_vectors)

ss = StandardScaler().fit(word_vectors_tsne)
word_vectors_tsne = ss.transform(word_vectors_tsne)

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 1000 samples in 0.001s...
[t-SNE] Computed neighbors for 1000 samples in 0.032s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1000
[t-SNE] Mean sigma: 0.054294
[t-SNE] Computed conditional probabilities in 0.050s
[t-SNE] Iteration 50: error = 60.6410446, gradient norm = 0.3141488 (50 iterations in 10.512s)
[t-SNE] Iteration 100: error = 56.7306557, gradient norm = 0.2477854 (50 iterations in 9.714s)
[t-SNE] Iteration 150: error = 56.0499115, gradient norm = 0.2580498 (50 iterations in 10.091s)
[t-SNE] Iteration 200: error = 55.3717346, gradient norm = 0.2453297 (50 iterations in 9.621s)
[t-SNE] Iteration 250: error = 54.8031044, gradient norm = 0.2608456 (50 iterations in 9.518s)
[t-SNE] KL divergence after 250 iterations with early exaggeration: 54.803104
[t-SNE] Iteration 300: error = 0.8770762, gradient norm = 0.0010110 (50 iterations in 9.120s)
[t-SNE] Iteration 350: error = 0.8026948, gradient norm = 0.000

In [30]:
output_notebook()
draw_vectors(word_vectors_tsne[:, 0], word_vectors_tsne[:, 1], token=words)

Loading BokehJS ...

Figure(id='1115', ...)

In [14]:
import gensim.downloader as api
pre_model = api.load('word2vec-ruscorpora-300')

In [15]:
wordic =preprocess_text('хочу')
model_w2v.get_vector(wordic)
print(*model_w2v.most_similar(positive=[wordic]))
print("vs ruscorpora")
word ='хотеть_VERB'
pre_model.get_vector(word)
print(*pre_model.most_similar(positive=[word]))


('изменяться', 0.9871472716331482) ('ценить', 0.9749559760093689) ('милый', 0.9732074737548828) ('получаться', 0.972845196723938) ('сбываться', 0.9724627733230591) ('означать', 0.9719640612602234) ('кричать', 0.9718726873397827) ('злословие', 0.9704494476318359) ('красивый', 0.9704354405403137) ('посмотреть', 0.9702513813972473)
vs ruscorpora
('захотеть_VERB', 0.7732996940612793) ('желать_VERB', 0.7239466905593872) ('хотеться_VERB', 0.7220498323440552) ('захотеться_VERB', 0.62186598777771) ('полюбин_NOUN', 0.6022353172302246) ('нужно_ADV', 0.6014082431793213) ('валерьяна::александрыч_NOUN', 0.5812994241714478) ('фрейлен::минный_NOUN', 0.5723892450332642) ('юрьюшка_NOUN', 0.5544917583465576) ('вздумать_VERB', 0.5534098148345947)


Далее следуют эксперименты с Doc2vec

In [16]:
#preparing data for doc2vec
def tagged_document(list_of_list_of_words):
    for i, list_of_words in enumerate(list_of_list_of_words):
        yield gensim.models.doc2vec.TaggedDocument(list_of_words, [i])
quotes_for_training = list(tagged_document(quote_tokens))


In [20]:
model = gensim.models.doc2vec.Doc2Vec.load('models/d2v_v1-0.model')

In [58]:
#buiding a model
model = gensim.models.doc2vec.Doc2Vec(vector_size=40, min_count=2, epochs=30)
model.build_vocab(quotes_for_training)
model.train(quotes_for_training, total_examples=model.corpus_count, epochs=model.epochs)

In [21]:
print(model.infer_vector(['любить', 'кататься', 'любить', 'сани', 'возить']))
print(quote_tokens[0])

[ 0.02300859  0.07611404 -0.01230096  0.0507215  -0.05635476 -0.11815231
  0.0255346  -0.02589718 -0.02916602  0.02253626  0.1227912  -0.13495131
 -0.01224023 -0.00672684  0.15623629  0.11219501 -0.06968729 -0.09525655
  0.04249541 -0.11932426 -0.03011477  0.00089069  0.10288895  0.01741376
 -0.14537834 -0.06388635 -0.0270704   0.29518172 -0.13122255 -0.03525008
  0.11814627  0.06011065  0.0642923  -0.0214094   0.03768281  0.12861484
  0.33758008 -0.07298842 -0.11856309 -0.1995531 ]
['выкидывать', 'твой', 'мысль', 'грусть', 'пустота', 'печаль', 'помнить', 'подарить', 'лето', 'время', 'февраль']


In [23]:
#vectors of quotes for visualization
quote_vectors = [model.infer_vector(q) for q in quote_tokens]

In [44]:
#downsizing decompozition and later vectors ploting on the plane
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

pca = PCA(n_components=40)
pca.fit(quote_vectors)
word_vectors_pca = pca.transform(quote_vectors)
ss = StandardScaler().fit(word_vectors_pca)
word_vectors_pca = ss.transform(word_vectors_pca)

In [65]:
import bokeh.models as bm, bokeh.plotting as pl
from bokeh.io import output_notebook
output_notebook()

def draw_vectors(x, y, radius=10, alpha=0.25, color='blue',
                 width=600, height=400, show=True, **kwargs):
    if isinstance(color, str): color = [color] * len(x)
    data_source = bm.ColumnDataSource({ 'x' : x, 'y' : y, 'color': color, **kwargs })

    fig = pl.figure(active_scroll='wheel_zoom', width=width, height=height)
    fig.scatter('x', 'y', size=radius, color='color', alpha=alpha, source=data_source)

    fig.add_tools(bm.HoverTool(tooltips=[(key, "@" + key) for key in kwargs.keys()]))
    if show: pl.show(fig)
    return fig


draw_vectors(word_vectors_pca[:, 0], word_vectors_pca[:, 1], token=quote_tokens)

Loading BokehJS ...

Figure(id='1370', ...)

In [66]:
ranks = []
second_ranks = []
for doc_id in range(len(quotes_for_training)):
    inferred_vector = model.infer_vector(quotes_for_training[doc_id].words)
    sims = model.dv.most_similar([inferred_vector], topn=len(model.dv))
    rank = [docid for docid, sim in sims].index(doc_id)
    ranks.append(rank)

    second_ranks.append(sims[1])

In [67]:
import collections

counter = collections.Counter(ranks)
print(counter)

Counter({0: 7585, 1: 1000, 2: 465, 3: 318, 4: 220, 5: 191, 6: 159, 8: 115, 7: 114, 10: 92, 9: 92, 12: 82, 13: 66, 11: 65, 14: 62, 16: 58, 17: 56, 15: 51, 18: 47, 19: 45, 24: 41, 25: 39, 20: 33, 21: 30, 22: 29, 33: 28, 39: 27, 23: 26, 27: 24, 26: 23, 28: 23, 30: 23, 35: 22, 29: 21, 34: 19, 31: 18, 42: 17, 49: 17, 32: 16, 40: 16, 46: 15, 41: 15, 47: 15, 56: 14, 45: 14, 44: 14, 36: 14, 54: 13, 38: 13, 69: 12, 61: 12, 55: 12, 57: 11, 64: 11, 37: 11, 53: 11, 43: 11, 51: 10, 84: 10, 68: 10, 74: 10, 63: 9, 60: 9, 52: 9, 94: 9, 48: 9, 67: 9, 70: 8, 73: 8, 91: 7, 92: 7, 99: 7, 78: 7, 72: 6, 93: 6, 112: 6, 90: 6, 65: 6, 88: 6, 79: 6, 114: 6, 66: 6, 81: 6, 113: 5, 58: 5, 111: 5, 115: 5, 80: 5, 59: 5, 62: 5, 76: 5, 107: 5, 103: 5, 71: 5, 137: 5, 122: 5, 50: 5, 136: 5, 145: 4, 116: 4, 146: 4, 97: 4, 89: 4, 109: 4, 77: 4, 225: 4, 151: 4, 95: 4, 75: 4, 82: 4, 110: 4, 105: 4, 235: 4, 96: 4, 149: 4, 86: 4, 415: 3, 214: 3, 148: 3, 203: 3, 252: 3, 202: 3, 127: 3, 120: 3, 210: 3, 132: 3, 243: 3, 131: 3, 9

In [24]:
#inferred_vector = model.infer_vector(quotes_for_training[0].words)
q_num = 1045
sim = model.dv.most_similar(model.infer_vector(quotes_for_training[q_num].words), topn=10)
#print(quote_tokens[q_num])
print(" ".join(quote_words[q_num]))
print("\n -------------------------------------------------suggestions----------------------------------------------\n")
for quote in sim:
    #print(quote_tokens[quote[q_num]], round(quote[1], 3))
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3))

Человек всегда находит ложь, которая ему необходима, причем так же точно и быстро, как и необходимую ему правду, если вообще ощущает необходимость в правде.

 -------------------------------------------------suggestions----------------------------------------------

Человек всегда находит ложь, которая ему необходима, причем так же точно и быстро, как и необходимую ему правду, если вообще ощущает необходимость в правде. 0.941
Искажая правду-порождаем ложь. 0.808
Без дара убеждения правда иногда выглядит жалкой. 0.79
Своя правда дороже чужой истины! 0.789
Своя правда дороже чужой истины! 0.785
Честность есть простейшее выражение принципа правды. 0.784
Ищите же прежде Царства Божия и правды Его, и это все приложится вам. 0.78
Если ты закроешь свою дверь для всех заблуждений, то и правда останется снаружи. 0.78
Правды в чистом виде не существует. Она всегда в той или иной степени разбавлена ложью. 0.779
Ложь, повторенная тысячу раз, становится правдой. 0.778


In [91]:
model.save('models/d2v_v1-0.model')

In [25]:
#request handling
request = preprocess_text(input()).split()
sim = model.dv.most_similar(model.infer_vector(request), topn=10)

print("\n -------------------------------------------------wise response----------------------------------------------\n")
for quote in sim:
    #print(quote_tokens[quote[q_num]], round(quote[1], 3))
    print(" ".join(quote_words[quote[0]]), round(quote[1], 3))

почему так тяжело жить?

 -------------------------------------------------wise response----------------------------------------------

Мы не вправе жить, когда погибла честь. 0.777
Легендами становятся те кто, живут самим собой уважая себя! 0.768
Жестоким стало не общество,жестокими стали мы. 0.762
Человек не может жить без уверенности в том, что он кому-то нужен, что его любят. 0.754
Когда кто-то говорит, что научился жить без тебя. Ты уже в дураках, чтобы ты ни сказал. 0.731
Не учите меня жить, лучше помогите материально! 0.729
Есть люди столь скупые, как если бы они собирались жить вечно, и столь расточительные, как если бы собирались умереть завтра. 0.725
С дураками жить намного проще,им не надо навязывать себя. 0.718
Если рабы будут ждать свободы до тех пор, пока они не поумнеют, ждать придется долго... 0.718
Есть люди столь скупые, как если бы они собирались жить вечно, и столь расточительные, как если бы собирались умереть завтра. 0.716


Подготовка к мерджу, эссенсия функционала по функциям:


In [36]:
qoute_path = '../parsing/data/cleaned_tagged.txt'

df = pd.read_csv(qoute_path, sep='<\d*>', engine ='python', names=['quotes']) #reading quotes to the dataframe
with open(qoute_path, 'r', encoding='utf-8') as file:
    data = file.read().replace('\n', ' nextquote ')
    processed_data = preprocess_text(data)  #preprocessing qoutes
#dataframe with quotes and their processed versions
df.insert(loc=1, column="processed_quotes", value=processed_data.split('nextquote')[:-1], allow_duplicates=True) 

df.to_csv('processed_q.csv', columns=['quotes', 'processed_quotes'], index=False)

Libriaris:

In [ ]:
#preprocessing libriaris
import nltk
nltk.download("stopwords")
#stopwords modules
from nltk.corpus import stopwords
from pymystem3 import Mystem
from string import punctuation
#pandas
import pandas as pd
import numpy as np
import io


Files loading:

In [42]:
#files:
#Create lemmatizer and stopwords list
mystem = Mystem() 
russian_stopwords = stopwords.words("russian")

df = pd.read_csv('processed_q.csv', engine ='python')

Funcions:

In [ ]:
#Preprocess function (stopwords, puncuation, etc)
def preprocess_text(text):
    tokens = mystem.lemmatize(text.lower())
    tokens = [token for token in tokens if token not in russian_stopwords\
              and token != " " \
              and token.strip() not in punctuation]   
    text = " ".join(tokens)    
    return text

#preparing data for doc2vec
def tagged_document(list_of_list_of_words):
    for i, list_of_words in enumerate(list_of_list_of_words):
        yield gensim.models.doc2vec.TaggedDocument(list_of_words, [i])
    quotes_for_training = list(tagged_document(quote_tokens))




main